In [2]:
import pyforest
from rdkit import Chem
from rdkit.Chem import AllChem
from imblearn.over_sampling import SMOTEN, ADASYN, SMOTE 

In [3]:
data_path = '../datasets/original_datasets/'

In [4]:
test = pd.read_csv(data_path+'NEK2_1_uM_min_50_pct_binding.csv')
test

<IPython.core.display.Javascript object>

target_name compound_id  \
0           NEK2      kdb_10   
1           NEK2     kdb_100   
2           NEK2    kdb_1003   
3           NEK2     kdb_101   
4           NEK2     kdb_102   
...          ...         ...   
1403        NEK2     kdb_976   
1404        NEK2      kdb_98   
1405        NEK2     kdb_980   
1406        NEK2     kdb_986   
1407        NEK2      kdb_99   

                                      base_rdkit_smiles  pct_binding  active  
0     CCS(=O)(=O)N1CC(CC#N)(n2cc(-c3ncnc4[nH]ccc34)c...     3.225806       0  
1     C[C@@H](Oc1cc(C(=O)Nc2ccc(C(=O)N3CCN(C)CC3)cc2...     3.225806       0  
2     CC1(O)CC(c2nc(-c3ccc4ccc(-c5ccccc5)nc4c3)c3c(N...     5.000000       0  
3     COCC(=O)NC/C=C/c1ccc2ncnc(Nc3ccc(Oc4ccc(C)nc4)...     6.158358       0  
4     COC(=O)c1ccc2c(c1)NC(=O)/C2=C(\Nc1ccc(N(C)C(=O...     6.158358       0  
...                                                 ...          ...     ...  
1403                       Oc1c2ccccc2c2c3c(cccc13)N=N2     9.090909       0  
1404  Cc1nc(Nc2n[nH]c3c2CN(C(=O)N[C@H](CN(C)C)c2cccc...     3.225806       0  
1405  Cc1cnc(-c2cnc(NCCNc3ccc(C#N)cn3)nc2-c2ccc(Cl)c...    85.000000       1  
1406            Nc1n[nH]c2nnc(-c3ccccc3)c(-c3ccccc3)c12     0.000000       0  
1407  C[C@@H](Oc1cc(-n2cnc3ccc(CN4CCN(C)CC4)cc32)sc1...    79.365079       1  

[1408 rows x 5 columns]

In [ ]:
def check_labels(data_path, filename): 

  
    df = pd.read_csv(data_path+filename)

    pct_col = [col for col in df.columns if col.startswith('pct_')] 
    len(pct_col) == 1 
    pct_col = pct_col[0]
    invalid_labels = df[df['active']!= (df[pct_col]>=50).astype(int)]
    if invalid_labels.empty: 
        # print(f'correct label assignment based on {pct_col} column')
        pass
    else: 
        print(f'Error on label assignement.')
        print(invalid_labels)
    # check for duplicates here 
    duplicates = df[df.duplicated()]
    print(f'{df.shape}')
    #duplicates = df[df.duplicated(subset=['base_rdkit_smiles'])]
   
    if not duplicates.empty:
        print('Duplicate rows found:')
        print(duplicates)
        df_cleaned = df.drop_duplicates()
        print(f'df size original: {df.shape}')
        print(f'remove duplicates. {df_cleaned.shape}')
check_labels(data_path,'NEK2_1_uM_min_50_pct_inhibition.csv')

In [ ]:
#create a dataset with folds

# must specify filename because the 50pct binding and inhibition files differ
# to-do: discuss how to do this --> this will create a file that is just this but with column specifying split
#       do we want to already integrate a split_uuid like AMPL? 
#       additionally, we still have to use the splits to create the "scaled df" 
def remove_duplicates(datapath, filename):
    df = pd.read_csv(f'{datapath}{filename}')
    duplicates = df.duplicated(subset=['base_rdkit_smiles'])
    if duplicates.any():
        print('Duplicate rows found:')
        print(df[duplicates])
        df_cleaned = df.drop_duplicates(subset=['base_rdkit_smiles'])
        print(f'df size original: {df.shape}')
        print(f'Removed duplicates. New df size: {df_cleaned.shape}')
    else: 
        df_cleaned = df
    return df_cleaned
    
def create_folds(datapath, filename, k_splits): 
    """filename: NEK#_1_uM_min_50_pct_(binding or inhibition).csv"""
    df = remove_duplicates(datapath, filename)
    # is this extra/too much and should we just assume what labels coincide with majority and minority? 
    # determine majority/minority class 
    #       AMPL takes in 'response column' 
    class_labels = df['active'].value_counts() 
    print(class_labels)
    if len(class_labels)>1: 
        majority_class_label =class_labels.idxmax() 
        majority_num = class_labels.max() 
        minority_class_label = class_labels.idxmin()
        minority_count = class_labels.min()
    df_majority = df[df['active']==majority_class_label]
    df_minority=df[df['active']==minority_class_label]
    # copy to avoid warnings 
    df_majority = df_majority.copy()
    df_minority = df_minority.copy()
    kf = KFold(k_splits,shuffle=True, random_state=42)
    # majority 
    for i, (_, v_ind) in enumerate(kf.split(df_majority)):
        df_majority.loc[df_majority.index[v_ind], 'fold'] = f"fold{i+1}"
    # minority 
    for i, (_, v_ind) in enumerate(kf.split(df_minority)):
        df_minority.loc[df_minority.index[v_ind], 'fold'] = f"fold{i+1}"
    all_fold_df = pd.concat([df_majority,df_minority])
    
    print(all_fold_df.shape)
    print(all_fold_df.active.value_counts())
    ## actually, this might be perfect jsut to save as "split df" because then 
    # in the next step of creating a dataset, you can choose what fold you want to be the test set 
    return all_fold_df
        
    

In [ ]:
call in create_folds labeled with nek_folded 
    then call train_and__ to get full 80% train and do not touch 20% 
        then get 80% train and call create_folds
            then send to a seperate directory call K-fold 
    
in the the K-fold directory use the data that is folded called train___ 
    use to make train and test with each fold

In [ ]:
def train_and__(data_path, fold_df, test_fold):
   """function to label 'train' or 'test' in the 'subset' column
   to be used to create train/test OR train/val
   fold_df: dataframe with column 'fold'
   test_fold (str): fold to make the test set (the remaining folds will be train)
   """
   df = pd.read_csv(data_path+fold_df) 
   df['subset'] = df['fold'].apply(lambda x: 'test' if x == test_fold else 'train')

   return df[['NEK','compound_id', 'active', 'base_rdkit_smiles', 'subset']]



In [ ]:
def get_bind_inhib(df_name):
    match = re.search(r'_([^_]+)\.csv$',df_name)
    return match.group(1) if match else None
    # returns 'binding' or 'inhibition' 
og_dfs = [file for file in os.listdir(data_path) if file.startswith('NEK')]

for df in og_dfs: 
    folded_df = create_folds(data_path, df,5)
    bind_inhib = get_bind_inhib(df)
    nek_name = f'NEK{df[3]}_{bind_inhib}'
    print(nek_name)
    folded_df['NEK']=nek_name 
    folded_df.to_csv(f'../datasets/initial_fold/{nek_name}_initial_fold.csv',index=False)

    # folded_df.to_csv('intial_fold')

# def label_train_validation(data_path, train80df, fold)
#     return train df with folds

In [21]:
neks = ['NEK2_binding', 'NEK2_inhibition', 'NEK3_binding', 'NEK5_binding','NEK9_binding','NEK9_inhibition']

for nek in neks:
    fold_df_name = nek+"_initial_fold.csv"
    print(fold_df_name)
    labeled_df = train_and__("/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/initial_fold/" , fold_df_name, "fold1")
    labeled_df.to_csv(f'/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/{nek}_80_20_df.csv',index=False)
#labeled_df
    



NEK2_binding_initial_fold.csv


<IPython.core.display.Javascript object>

NEK2_inhibition_initial_fold.csv


<IPython.core.display.Javascript object>

NEK3_binding_initial_fold.csv


...

<IPython.core.display.Javascript object>

NEK9_binding_initial_fold.csv


<IPython.core.display.Javascript object>

NEK9_inhibition_initial_fold.csv


<IPython.core.display.Javascript object>

In [ ]:
#featurize 
def featurize(data_path, filename, feat_type, moe_path=None, moe_file=None, mfp_radius=2, nBits=2048): 
    if (feat_type == 'MOE') and (moe_path is not None) and (moe_file is not None): 
        df = create_moe(data_path, filename, moe_path, moe_file)
    elif feat_type == 'MFP': 
        df = create_mfp(data_path, filename, mfp_radius, nBits)
    
    return df


In [ ]:
def create_moe(data_path, filename, moe_path, moe_file):
    """(intended use for already existing dataset)
    This function will use an existing dataframe with smiles column to
    get the features from an existing file (moe_path+moe_file) with the MOE features generated"""
    
    drop_cols = ['active', 'compound_id']
    df = remove_duplicates(data_path, filename)
    df=df.drop(columns=drop_cols)
    

    moe_df=remove_duplicates(moe_path,moe_file)
    

    final_df=moe_df.merge(df, how='outer', on=['base_rdkit_smiles'], suffixes=('_moe_desc', '_og'))
    id_cols = ['NEK', 'compound_id','base_rdkit_smiles','subset', 'active']
    feat_cols = set(list(final_df.columns))-set(id_cols)
    
    final_order_cols = list(id_cols)+list(feat_cols)


    return final_df[final_order_cols]
    # in production code , check for smiles col 

test_df = featurize('/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/','NEK2_inhibition_80_20_df.csv', 'MOE','/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/original_datasets/scaled_descriptors/' , 'NEK2_1_uM_min_50_pct_inhibition_with_moe_descriptors.csv')

In [ ]:
test_df

In [ ]:
def smiles_to_fps(smiles_list, radius=2, nBits=2048):
    fps = []
    for smi in smiles_list:
        mol = Chem.MolFromSmiles(smi)
        if mol is not None:
            fp = AllChem.GetMorganFingerprintAsBitVect(mol, radius, nBits=nBits)
            arr = np.zeros((1,), dtype=np.int8)
            Chem.DataStructs.ConvertToNumpyArray(fp, arr)
            fps.append(arr)
    return np.array(fps)


def create_mfp(file_path, filename, mfp_radius, nBits):
    df = pd.read_csv(file_path+filename)

    id_data = df[['compound_id','base_rdkit_smiles', 'NEK','subset','active']]
    smiles = df['base_rdkit_smiles']

    mfp_feats = smiles_to_fps(smiles,mfp_radius,nBits)
    mfp_df = pd.DataFrame(mfp_feats)

    id_cols = ['NEK', 'compound_id','base_rdkit_smiles','subset', 'active']
    feat_cols = set(list(mfp_df.columns))-set(id_cols)
    final_order_cols = list(id_cols)+list(feat_cols)
    final_df = pd.concat([mfp_df, df],axis=1)
    final_df = final_df[final_order_cols]
    display(final_df)

    
    # testX_mfp_df['active'] = test_y.reset_index(drop=True)
    # final_df = pd.concat([trainX_mfp_df,testX_mfp_df], ignore_index=True)
    return final_df
        

test_df = featurize('/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/','NEK2_inhibition_80_20_df.csv', 'MFP',2,2048 )

In [23]:
og_df_path = '/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/' 
scaled_desc_path = '/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/original_datasets/scaled_descriptors/'
featurized_filepath = '/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/featurized/' 
for nek in ['2','3','5','9']: 
    if nek in ['2','9']:
        bind_inhib = ['binding','inhibition']
    else: 
        bind_inhib = ['binding']
    for bi in bind_inhib: 

        for feat in ['MOE','MFP']: 
            print(f'NEK {nek} {bi} {feat}')
            og_df_name = f'NEK{nek}_{bi}_80_20_df.csv'
            if feat == 'MOE': 
                desc_filename =f'NEK{nek}_1_uM_min_50_pct_{bi}_with_moe_descriptors.csv'
                final_moe_df = featurize(og_df_path,og_df_name,feat,scaled_desc_path,desc_filename)
                final_moe_df.to_csv(f'{featurized_filepath}NEK{nek}_{bi}_{feat}_none_unscaled.csv',index=False)
                
            elif feat=='MFP': 
                final_mfp_df = featurize(og_df_path,og_df_name,feat,2,2048)
                final_mfp_df.to_csv(f'{featurized_filepath}NEK{nek}_{bi}_{feat}_none_unscaled.csv',index=False)



NEK 2 binding MOE


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

NEK 2 binding MFP


<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

NEK compound_id  \
0    NEK9_inhibition    kdb_1014   
1    NEK9_inhibition    kdb_1153   
2    NEK9_inhibition    kdb_1618   
3    NEK9_inhibition    kdb_2013   
4    NEK9_inhibition    kdb_2200   
..               ...         ...   
388  NEK9_inhibition    kdb_3769   
389  NEK9_inhibition    kdb_3771   
390  NEK9_inhibition    kdb_3772   
391  NEK9_inhibition    kdb_3774   
392  NEK9_inhibition    kdb_3775   

                                     base_rdkit_smiles subset  active  0  1  \
0            Nc1nccc(-c2c(-c3ccc(F)cc3)ncn2C2CCNCC2)n1  train       0  0  0   
1                  Cn1cc(C=C2C(=O)Nc3cccnc32)c2ccccc21  train       0  0  0   
2              COc1ccc(COc2ccc(Cc3cnc(N)nc3N)cc2OC)cc1  train       0  0  0   
3    NC(=O)c1ccc(-c2nc(-c3ccccn3)c(-c3ccc4c(c3)OCO4...   test       0  0  0   
4         c1ccc(Cc2nc3ccc(Nc4ncnc5ccccc45)cc3[nH]2)cc1  train       0  0  0   
..                                                 ...    ...     ... .. ..   
388  COc1cc(N2CCN(C)CC2)ccc1Nc1ncc2c(n1)n1c(cc3cccc...  train       1  0  0   
389  COc1cc(C(=O)N2CCC(N3CCN(C)CC3)CC2)ccc1Nc1ncc2c...  train       1  0  0   
390  CCOc1cc(N2CCC(O)CC2)ccc1Nc1ncc2c(n1)n1c(cc3ccc...   test       1  0  0   
391  COc1cc(N2CCOCC2)ccc1Nc1ncc2c(n1)N1c3ccccc3CC1C...  train       1  0  0   
392  CCn1c(=O)c2cc3ccccc3n2c2nc(Nc3ccc(N4CCN(C)CC4)...  train       1  0  0   

     2  3  4  ...  2038  2039  2040  2041  2042  2043  2044  2045  2046  2047  
0    0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
1    0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
2    0  0  0  ...     0     0     0     0     1     0     0     0     0     0  
3    0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
4    0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
..  .. .. ..  ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
388  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
389  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
390  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
391  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
392  0  0  0  ...     0     0     0     0     0     1     0     0     0     0  

[393 rows x 2053 columns]

In [25]:
neks

['NEK2_binding',
 'NEK2_inhibition',
 'NEK3_binding',
 'NEK5_binding',
 'NEK9_binding',
 'NEK9_inhibition']

In [44]:
#creating scalers for eack Nek
id_cols = ['NEK', 'compound_id','base_rdkit_smiles','subset', 'active']

featurized_filepath = '/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/featurized/' 
scaler_dir = '/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/scalers/'
for nek in neks: 
    for feat in ['MOE','MFP']: 
      
        df = pd.read_csv(f'{featurized_filepath}{nek}_{feat}_none_unscaled.csv')
        feat_cols = set(list(df.columns))-set(id_cols)
        train_x = df[df["subset"] == "train"]
        train_id = train_x[id_cols]
        train_x.drop(columns = id_cols, inplace=True)
        test_x = df[df["subset"] == "test"]
        test_id = test_x[id_cols]
        test_x.drop(columns = id_cols, inplace=True)
        
        scaling = StandardScaler()
        scaling.fit(train_x)
        #save to pickle
        with open(f'{scaler_dir}_{nek}_{feat}_scaler.pkl', 'wb') as f: 
            pickle.dump(scaling, f) 
        train_scaled = scaling.transform(train_x)
        test_scaled = scaling.transform(test_x)
        trainX_final = pd.DataFrame(train_scaled, columns=list(feat_cols))
        testX_final = pd.DataFrame(test_scaled, columns=list(feat_cols))
        scaled_data = pd.concat([trainX_final, testX_final])
        id_data = pd.concat([train_id,test_id])
        no_samp_data_scaled = pd.concat([id_data.reset_index(drop=True), scaled_data.reset_index(drop=True)], axis=1)
        no_samp_data_scaled.to_csv(f'{featurized_filepath}{nek}_{feat}_none_scaled.csv',index=False)




<IPython.core.display.Javascript object>

/var/folders/5p/_w9hrx997yb7f1_y_4_4k4bw0000gn/T/ipykernel_83439/1233867023.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_x.drop(columns = id_cols, inplace=True)
/var/folders/5p/_w9hrx997yb7f1_y_4_4k4bw0000gn/T/ipykernel_83439/1233867023.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_x.drop(columns = id_cols, inplace=True)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

NEK compound_id  \
0    NEK9_inhibition    kdb_1014   
1    NEK9_inhibition    kdb_1153   
2    NEK9_inhibition    kdb_1618   
3    NEK9_inhibition    kdb_2200   
4    NEK9_inhibition    kdb_2206   
..               ...         ...   
388  NEK9_inhibition    kdb_3756   
389  NEK9_inhibition    kdb_3757   
390  NEK9_inhibition    kdb_3761   
391  NEK9_inhibition    kdb_3762   
392  NEK9_inhibition    kdb_3772   

                                     base_rdkit_smiles subset  active  446  \
0            Nc1nccc(-c2c(-c3ccc(F)cc3)ncn2C2CCNCC2)n1  train       0  0.0   
1                  Cn1cc(C=C2C(=O)Nc3cccnc32)c2ccccc21  train       0  0.0   
2              COc1ccc(COc2ccc(Cc3cnc(N)nc3N)cc2OC)cc1  train       0  0.0   
3         c1ccc(Cc2nc3ccc(Nc4ncnc5ccccc45)cc3[nH]2)cc1  train       0  0.0   
4    COc1cc2ncn(-c3cc(O[C@@H](C)c4ccccc4Cl)c(C(N)=O...  train       0  0.0   
..                                                 ...    ...     ...  ...   
388  Cn1c(=O)c2cc3ccccc3n2c2nc(Nc3cc(N4CCOCC4)cc(N4...   test       1  0.0   
389  CCN1CCN(c2ccc(Nc3ncc4c(n3)n3c(cc5ccccc53)c(=O)...   test       1  0.0   
390   Cn1c(=O)c2cc3ccccc3n2c2nc(Nc3cnn(CC(F)F)c3)ncc21   test       1  0.0   
391  CN1CCN(c2ccc(Nc3ncc4c(n3)n3c(cc5ccccc53)c(=O)n...   test       1  0.0   
392  CCOc1cc(N2CCC(O)CC2)ccc1Nc1ncc2c(n1)n1c(cc3ccc...   test       1  0.0   

         1377      1699  1961  720  ...      1018  1456       840  297  \
0   -0.274957 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   
1   -0.274957 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   
2   -0.274957 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   
3   -0.274957 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   
4    3.636932 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   
..        ...       ...   ...  ...  ...       ...   ...       ...  ...   
388 -0.274957 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   
389 -0.274957 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   
390  3.636932 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   
391 -0.274957 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   
392 -0.274957 -0.080193   0.0  0.0  ... -0.080193   0.0 -0.056614  0.0   

          926       878      1664  1668       700   27  
0   -0.239651 -0.139800 -0.056614   0.0 -0.113776  0.0  
1   -0.239651 -0.139800 -0.056614   0.0 -0.113776  0.0  
2    4.172741 -0.139800 -0.056614   0.0 -0.113776  0.0  
3   -0.239651 -0.139800 -0.056614   0.0 -0.113776  0.0  
4   -0.239651 -0.139800 -0.056614   0.0 -0.113776  0.0  
..        ...       ...       ...   ...       ...  ...  
388 -0.239651 -0.139800 -0.056614   0.0 -0.113776  0.0  
389 -0.239651 -0.139800 -0.056614   0.0 -0.113776  0.0  
390 -0.239651 -0.139800 -0.056614   0.0 -0.113776  0.0  
391 -0.239651  7.153088 -0.056614   0.0 -0.113776  0.0  
392 -0.239651 -0.139800 -0.056614   0.0 -0.113776  0.0  

[393 rows x 2053 columns]

In [31]:
id_cols = ['NEK', 'compound_id', 'base_rdkit_smiles','subset', 'active'] 
def over_sampling(data_path,filename, sampling, NEK):
    """Oversample the datasetes using the SMOTE or ADASYN
    Keeps the feature names and id cols
    file_name (full/absolute path): use the scaled dataframe we just created above 'NEK#_(binding/inhibition)_(MOE/MFP)_none_scaled_df.csv'
    sampling (str): 'SMOTE' or 'ADASYN'
    returns: oversampled dataframe
    """
    
    df = pd.read_csv(data_path+filename) # this is the already scaled ver
    feat_cols = list(set(list(df.columns))-set(id_cols))
    
    # train and test 
    train = df[df['subset']=='train'] 
    test =df[df['subset']=='test'] 

    # separate just id cols
    just_ids = ['NEK', 'compound_id', 'base_rdkit_smiles','subset']
    train_just_ids = train[just_ids]
    test_just_ids = test[just_ids]

    # just feats and 'active'
    trainX = train[feat_cols]
    testX = test[feat_cols]
    
    trainy = train['active']
    testy = test['active']
    
    if sampling == 'ADASYN':
        oversample = ADASYN(random_state=42)
    else: 
        oversample = SMOTE(random_state=42)

    
    trainX_temp, trainy_temp = oversample.fit_resample(trainX.to_numpy(), trainy.to_numpy().reshape(-1))
    print(f'train after {sampling}: {trainX_temp.shape}')
    
    trainX_resamp = pd.DataFrame(trainX_temp, columns=feat_cols)
    trainy_resamp = pd.DataFrame(trainy_temp, columns=['active'])

    num_real = len(train)
    num_synthetic = len(trainX_resamp)-num_real
    synthetic_ids = pd.DataFrame({'NEK': [NEK] * num_synthetic,
        'compound_id': [f'synethic_{sampling}_{i}' for i in range(num_synthetic)],
        'base_rdkit_smiles': [f'synethic_{sampling}'] * num_synthetic,
        'subset': ['train']*num_synthetic}) # ,'active':[1]*num_synthetic}

    real_ids = train_just_ids.reset_index(drop=True)
    combined_ids = pd.concat([real_ids,synthetic_ids], ignore_index=True)
    
    train_resamp = pd.concat([combined_ids, trainX_resamp, trainy_resamp[['active']]], axis=1)

    print(train_resamp.columns[train_resamp.columns.duplicated()])
    test_df_final = pd.concat([test_just_ids.reset_index(drop=True),
                               testX.reset_index(drop=True), testy.reset_index(drop=True)],axis=1)

    
    
    # test_df_final['subset'] = 'test'
    # train_resamp = train_resamp.reindex(columns=df.columns)
    # test_df_final = test_df_final.reindex(columns=df.columns)
    
    
    final_df = pd.concat([train_resamp, test_df_final]).reset_index(drop=True)


    return final_df

In [42]:
# over_sampling(featurized_filepath, 'NEK2_binding_MFP_none_scaled.csv', "SMOTE", "NEK2_binding")
testing_jaycee = over_sampling('/Users/jayceepang/msse/capstone/atom2024/atom2024/notebooks/paper/datasets/80train_20test/featurized/', 'NEK2_binding_MOE_none.csv', "SMOTE", "NEK2_binding")

<IPython.core.display.Javascript object>

train after SMOTE: (2160, 306)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

Index([], dtype='object')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

NEK compound_id  \
0     NEK2_binding    kdb_2536   
1     NEK2_binding    kdb_3056   
2     NEK2_binding    kdb_3510   
3     NEK2_binding    kdb_3024   
4     NEK2_binding    kdb_2135   
...            ...         ...   
2438  NEK2_binding    kdb_2800   
2439  NEK2_binding    kdb_2110   
2440  NEK2_binding    kdb_2993   
2441  NEK2_binding    kdb_2219   
2442  NEK2_binding    kdb_2275   

                                      base_rdkit_smiles subset  PEOE_VSA+6  \
0     FC(F)(F)c1ccc(/C=C/c2cncnc2Nc2ccc3[nH]c(Cc4ccc...  train    9.045502   
1     CNCc1ccc(-c2cc(-c3nc(-c4ccc(S(=O)(=O)C(C)C)cc4...  train   17.238026   
2     CNC(=O)Nc1ccc2c(c1)CC[C@@]21OC(=O)N(CC(=O)N(Cc...  train   45.685555   
3                       CCCNc1ccc2ncc(-c3ccnc(C)c3)n2n1  train   17.238026   
4              O=C(O)c1ccc2c(c1)nc(NCc1ccccc1)c1ncncc12  train    0.000000   
...                                                 ...    ...         ...   
2438  Cc1ccc(NC(=O)Nc2ccc(Cl)cc2)cc1-c1ccc(C(=O)Nc2c...   test   26.059555   
2439               Cc1ccc2nc(Nc3cnn(C)c3)c3ncc(C)n3c2c1   test   28.428589   
2440  CN1CCN(c2cc(C(=O)Nc3ncc(SCc4c(F)cccc4F)s3)ccn2...   test    8.619013   
2441      COc1cc2ncnc(Nc3ccc4c(cnn4Cc4ccccc4)c3)c2cc1OC   test    0.000000   
2442  COC[C@@H](C)N[C@H]1CC[C@H](Nc2cc(-c3cccc(NCC4(...   test   17.238026   

      PEOE_VSA-2  vol_per_atom  b_heavy_per_atom  vsurf_EDmin1  a_base  ...  \
0       0.000000      7.788636          0.709091     -2.697009     0.0  ...   
1       6.512799      7.368644          0.610169     -2.585485     1.0  ...   
2       0.000000      7.306452          0.661290     -2.971039     0.0  ...   
3       0.000000      7.259868          0.578947     -2.358330     2.0  ...   
4       0.000000      7.960526          0.736842     -2.745083     0.0  ...   
...          ...           ...               ...           ...     ...  ...   
2438    0.000000      7.820455          0.654545     -2.535864     2.0  ...   
2439    0.000000      7.625000          0.641026     -2.644257     2.0  ...   
2440   19.760618      7.738208          0.641509     -3.341413     1.0  ...   
2441    0.000000      7.862981          0.673077     -2.678036     0.0  ...   
2442    0.000000      6.896959          0.527027     -2.972217     1.0  ...   

       SMR_VSA2  vsurf_Wp1_per_atom  PEOE_VSA+4   dipoleZ  diameter_per_atom  \
0     24.545046           21.538636    0.000000  0.902451           0.363636   
1      1.550734           25.197034    0.000000  0.060750           0.322034   
2     34.891285           19.405242   12.949531  0.031080           0.306452   
3     18.010750           21.700658    0.000000 -0.779117           0.289474   
4      0.000000           27.493421    0.000000 -1.574776           0.315789   
...         ...                 ...         ...       ...                ...   
2438   0.000000           25.270455    0.000000 -7.193194           0.363636   
2439   0.000000           23.301282   11.190562 -0.676505           0.282051   
2440  21.366350           22.082547   19.760618 -3.325952           0.339623   
2441   0.000000           20.413462    0.000000 -0.534155           0.326923   
2442   0.000000           16.655405    0.000000 -3.838224           0.283784   

      b_double  vsurf_W2_per_atom  vsurf_W6  Kier2_per_atom  active  
0          1.0          16.777273    22.750        0.222545       0  
1          0.0          17.114407    23.500        0.192759       0  
2          4.0          17.639113    25.750        0.201202       0  
3          2.0          14.075658     6.375        0.180000       0  
4          1.0          22.434211    36.875        0.219662       0  
...        ...                ...       ...             ...     ...  
2438       2.0          16.715909    19.000        0.232873       0  
2439       1.0          14.471154    12.375        0.157330       0  
2440       1.0          16.504717    15.375        0.215499       0  
2441       0.0          13.918269    16.125        0.202079

In [43]:

print(testing_jaycee['subset'].value_counts())
print(testing_jaycee[testing_jaycee['subset']=='train']['active'].value_counts())
print(testing_jaycee[testing_jaycee['subset']=='test']['active'].value_counts())

subset
train    2160
test      283
Name: count, dtype: int64
active
0    1080
1    1080
Name: count, dtype: int64
active
0    271
1     12
Name: count, dtype: int64
